In [29]:

from dotenv import load_dotenv
from llama_index.core.agent import ReActAgent

import os
load_dotenv()

os.environ['GOOGLE_API_KEY']  = os.getenv('GOOGLE_API_KEY')
if os.getenv('GOOGLE_API_KEY') != 'YOUR_API_KEY':
    print('API LOADED')
else:
    print("PLEASE ADD API")


API LOADED


In [30]:
import google.generativeai as genai

for m in genai.list_models():
    if "generateContent" in m.supported_generation_methods:
        print(m.name)

f:\Devfolio_hack\devfolio_hackathon-Cyber-AI\dev_env\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


models/gemini-1.0-pro-latest
models/gemini-1.0-pro
models/gemini-pro
models/gemini-1.0-pro-001
models/gemini-1.0-pro-vision-latest
models/gemini-pro-vision
models/gemini-1.5-pro-latest
models/gemini-1.5-pro-001
models/gemini-1.5-pro-002
models/gemini-1.5-pro
models/gemini-1.5-pro-exp-0801
models/gemini-1.5-pro-exp-0827
models/gemini-1.5-flash-latest
models/gemini-1.5-flash-001
models/gemini-1.5-flash-001-tuning
models/gemini-1.5-flash
models/gemini-1.5-flash-exp-0827
models/gemini-1.5-flash-8b-exp-0827
models/gemini-1.5-flash-8b-exp-0924
models/gemini-1.5-flash-002


In [31]:
from llama_index.llms.gemini import Gemini

gemma_llm = Gemini(model='models/gemini-1.5-flash',temperature=0.8,max_tokens=200000)

In [39]:
gemma_llm.complete("Whats Up bro").text

'Hey there!  How are you doing today? \n'

In [32]:
from llama_index.core import SimpleDirectoryReader

reader = SimpleDirectoryReader(input_files=["Data\cybersecurity_logs.txt"])
documents = reader.load_data()

In [33]:
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
embed_model = HuggingFaceEmbedding(model_name='BAAI/bge-small-en-v1.5')

In [34]:
from llama_index.core.node_parser import (
    SentenceSplitter,
    SemanticSplitterNodeParser,
)

splitter = SemanticSplitterNodeParser(
    buffer_size=1, breakpoint_percentile_threshold=10, embed_model=embed_model
)

nodes = splitter.get_nodes_from_documents(documents,show_progress=True)

Parsing nodes: 100%|██████████| 1/1 [00:07<00:00,  7.05s/it]


In [35]:
print(len(nodes))

1


In [36]:
for i in nodes:
    print(f"*******{i.metadata['file_name']}********: \n{i.get_content()}")
    print(len(i.get_content()))

*******cybersecurity_logs.txt********: 
2024-09-22 15:04:10,688 - INFO - Cybersecurity logging started...
2024-09-22 15:04:11,693 - INFO - CPU Usage: 4.8% | Memory Usage: 51.2%
2024-09-22 15:04:11,701 - INFO - Process: PID=0, Name=System Idle Process, User=NT AUTHORITY\SYSTEM
2024-09-22 15:04:11,791 - INFO - Process: PID=4, Name=System, User=NT AUTHORITY\SYSTEM
2024-09-22 15:04:11,796 - INFO - Process: PID=88, Name=, User=None
2024-09-22 15:04:11,800 - INFO - Process: PID=156, Name=Registry, User=None
2024-09-22 15:04:11,800 - INFO - Process: PID=516, Name=conhost.exe, User=PACMANEEE\Pranav
2024-09-22 15:04:11,804 - INFO - Process: PID=572, Name=smss.exe, User=None
2024-09-22 15:04:11,809 - INFO - Process: PID=632, Name=winlogon.exe, User=None
2024-09-22 15:04:11,813 - INFO - Process: PID=796, Name=services.exe, User=None
2024-09-22 15:04:11,817 - INFO - Process: PID=824, Name=LsaIso.exe, User=None
2024-09-22 15:04:11,821 - INFO - Process: PID=832, Name=svchost.exe, User=None
2024-09-2

In [37]:
splitter2 = SentenceSplitter(chunk_size = 2000,chunk_overlap=200)
nodes2 = splitter2.get_nodes_from_documents(documents,show_progress=True)

print(len(nodes2))
for i in nodes2:
    print(f"*******{i.metadata['file_name']}********: \n{i.get_content()}")
    print(len(i.get_content()))

Parsing nodes: 100%|██████████| 1/1 [00:04<00:00,  4.62s/it]

433
*******cybersecurity_logs.txt********: 
2024-09-22 15:04:10,688 - INFO - Cybersecurity logging started.
2024-09-22 15:04:11,693 - INFO - CPU Usage: 4.8% | Memory Usage: 51.2%
2024-09-22 15:04:11,701 - INFO - Process: PID=0, Name=System Idle Process, User=NT AUTHORITY\SYSTEM
2024-09-22 15:04:11,791 - INFO - Process: PID=4, Name=System, User=NT AUTHORITY\SYSTEM
2024-09-22 15:04:11,796 - INFO - Process: PID=88, Name=, User=None
2024-09-22 15:04:11,800 - INFO - Process: PID=156, Name=Registry, User=None
2024-09-22 15:04:11,800 - INFO - Process: PID=516, Name=conhost.exe, User=PACMANEEE\Pranav
2024-09-22 15:04:11,804 - INFO - Process: PID=572, Name=smss.exe, User=None
2024-09-22 15:04:11,809 - INFO - Process: PID=632, Name=winlogon.exe, User=None
2024-09-22 15:04:11,813 - INFO - Process: PID=796, Name=services.exe, User=None
2024-09-22 15:04:11,817 - INFO - Process: PID=824, Name=LsaIso.exe, User=None
2024-09-22 15:04:11,821 - INFO - Process: PID=832, Name=svchost.exe, User=None
2024-09

In [38]:
from llama_index.core import VectorStoreIndex,SummaryIndex
from llama_index.core import load_index_from_storage, StorageContext

if not os.path.exists('F:\Devfolio_hack\devfolio_hackathon-Cyber-AI\VectorData'):
    store = VectorStoreIndex(nodes2,embed_model=embed_model,show_progress=True)
    store.storage_context.persist(
        persist_dir='F:\Devfolio_hack\devfolio_hackathon-Cyber-AI\VectorData'
    )
else:
    store = load_index_from_storage(
                    StorageContext.from_defaults(persist_dir=f"F:\Devfolio_hack\devfolio_hackathon-Cyber-AI\VectorData"),
                    embed_model = embed_model
                )

summary_index = SummaryIndex(nodes2)


In [23]:
#DEPRECATED
# from llama_index.core import VectorStoreIndex,SummaryIndex
# from llama_index.core import load_index_from_storage, StorageContext

# if not os.path.exists('F:\Devfolio_hack\devfolio_hackathon-Cyber-AI\VectorData2'):
#     store2 = VectorStoreIndex(nodes,embed_model=embed_model,show_progress=True)
#     store2.storage_context.persist(
#         persist_dir='F:\Devfolio_hack\devfolio_hackathon-Cyber-AI\VectorData2'
#     )
# else:
#     store2 = load_index_from_storage(
#                     StorageContext.from_defaults(persist_dir=f"F:\Devfolio_hack\devfolio_hackathon-Cyber-AI\VectorData2"),
#                     embed_model = embed_model
#                 )

# summary_index2 = SummaryIndex(nodes)

Generating embeddings: 100%|██████████| 218/218 [00:22<00:00,  9.76it/s]


In [27]:
from llama_index.llms.groq import Groq
new_llm = Groq(model="llama3-70b-8192", api_key="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")
vqe = store.as_query_engine(llm=gemma_llm)
sqe = summary_index.as_query_engine(llm=gemma_llm)

In [68]:
#DEPRECATED
# vqe_semantic = store2.as_query_engine(llm=gemma_llm)
# sqe_semantic = summary_index2.as_query_engine(llm=new_llm)

In [16]:
res = sqe.query("As a Cyber Security expert give profesional thoughts about the activities of the computer with the failures, successes of the system")
print(res.response)

The computer system in question has a robust cybersecurity logging system in place, diligently recording process activity, network connections, and system resource usage. The system successfully identifies and records various processes running on the computer, including system processes, user-installed applications, and background tasks. 

While the system effectively logs network connections, highlighting active connections and their status, further analysis would be needed to determine potential vulnerabilities or suspicious activity. 

The logs demonstrate successful monitoring of CPU and memory usage, providing valuable insights into system performance and resource allocation. However, it would be beneficial to establish thresholds for these metrics and trigger alerts when they exceed predefined limits, potentially indicating malicious activity or system overload. 



In [55]:
from IPython.display import display, Markdown, Latex
def ChatWithLogs(prompt:str)->str:
    res = vqe.query(f"You are supposed to provide accurate answer in detail that answers the query, Query: {prompt}")

    display(Markdown(res.response))
    return res.response

In [56]:
ChatWithLogs("What are the overall summary of the cybersecurity logs")

The cybersecurity logs document a variety of system activities, including resource utilization, process information, and network connections.  The logs indicate that the system is running with a low CPU usage and moderate memory usage.  A range of processes, including system-related processes and user-specific applications, are active.  The logs also provide details about established network connections, both within the local machine and to external servers over the internet. 


'The cybersecurity logs document a variety of system activities, including resource utilization, process information, and network connections.  The logs indicate that the system is running with a low CPU usage and moderate memory usage.  A range of processes, including system-related processes and user-specific applications, are active.  The logs also provide details about established network connections, both within the local machine and to external servers over the internet. \n'

In [28]:
from llama_index.core.tools import QueryEngineTool

tools = [QueryEngineTool.from_defaults(name="vector_tool", description="This tool is used to understand specifics about the context",query_engine=vqe), QueryEngineTool.from_defaults(query_engine=sqe,name="summary_tool",description="This tool provides overall summary about the context")]

context = """
        Role: CyberSecurity Expert
        Instructions:
        - You are give have the tools vector_tool and summary_tool
        - According to the user query you will either have to create a Cyber Audit Report or provide information about the logs
        - Use the tools to get context and answer the user's query
        - Do not hallucinate context
        - Do not hallucinate user query
        - Do not deviate from the instructions and stick to the role
        - Follow the instructions 
        - Answer in detail to answer the user's query
        - Provide the complete output at the end
        - Provide detailed request as input to the tools
"""

In [44]:
from llama_index.llms.groq import Groq

new_llm = Groq(model="llama3-70b-8192", api_key="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")

agent = ReActAgent.from_tools(tools=tools,context=context,llm=gemma_llm,verbose=True,max_iterations=100)

NameError: name 'tools' is not defined

In [45]:
new_llm.complete('Whats up bro ?')

CompletionResponse(text="Not much bro! Just hanging out and ready to chat. How about you? What's new with you?", additional_kwargs={}, raw=ChatCompletion(id='chatcmpl-8563baba-f8c1-4698-9f5c-f4bb13dc78c9', choices=[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content="Not much bro! Just hanging out and ready to chat. How about you? What's new with you?", refusal=None, role='assistant', function_call=None, tool_calls=None))], created=1727448675, model='llama3-70b-8192', object='chat.completion', service_tier=None, system_fingerprint='fp_87cbfbbc4d', usage=CompletionUsage(completion_tokens=23, prompt_tokens=14, total_tokens=37, completion_tokens_details=None, queue_time=0.031580157, prompt_time=0.000772843, completion_time=0.075697439, total_time=0.076470282), x_groq={'id': 'req_01j8szdxk2ebrbks6sn7d3hehf'}), logprobs=None, delta=None)

In [84]:
res = agent.query("Analyze the processes of the system in detail and provide insights and a complete audit report about the system in markdown format, The markdown should contain the following sections: Overview, System Information,CPU  Usage, Memory Usage, Suspicious Processes, Security Reccomendations Conclusions. Get information about each for each of the sections")


> Running step 348cbf85-45ed-4450-9402-fc6564e0018e. Step input: Analyze the processes of the system in detail and provide insights and a complete audit report about the system in markdown format, The markdown should contain the following sections: Overview, System Information,CPU  Usage, Memory Usage, Suspicious Processes, Security Reccomendations Conclusions. Get information about each for each of the sections
Thought: I need to use a tool to get information about the system processes.
Action: vector_tool
Action Input: {'input': 'Analyze the processes of the system in detail and provide insights and a complete audit report about the system in markdown format. The markdown should contain the following sections: Overview, System Information,CPU  Usage, Memory Usage, Suspicious Processes, Security Reccomendations Conclusions. Get information about each for each of the sections'}
Observation: ## System Audit Report

**Overview**

This report provides an analysis of the system based on th

In [44]:
from llama_index.core.tools import FunctionTool
import getlogs


def file_expert(input:str)->str:
    """This is a function to retrieve information about files, and to generate whole audit report based on the logs"""
    permanent_prompt = "Analyze the processes of the system in detail and provide insights and a complete audit report about the system in markdown format, The markdown should contain the following sections: Overview, System Information,CPU  Usage, Memory Usage, Suspicious Processes, Security Reccomendations Conclusions. Get information about each for each of the sections"
    res = agent.query(f"{permanent_prompt} and also do the following, {input}")
    return res.response

file_expert_tool = FunctionTool.from_defaults(name='file_expert_tool',description="This is a function to retrieve information about files, and to generate whole audit report based on the logs",fn=file_expert)

def create_logs(input):
    """This tool is used to create logs from the existing computer and saves it in a file"""
    getlogs.main(max_count=1,time_interval=10)
    response = {}
    response['status'] = "NO FILE FOUND, ERRROR"
    response['filename'] = False
    if os.path.exists('Data\cybersecurity_logs_structured.csv'):
        with open('Data\cybersecurity_logs_structured.csv','r') as f:
            res = f.read()
        response['status'] = 'File Created'
        response['filename'] = 'Data\cybersecurity_logs_structured.csv'
    return str(response)

create_logs_tool = FunctionTool.from_defaults(name='create_logs_tool',description="This tool is used to create logs from the existing computer and saves it in a file",fn=create_logs)
detect_danger_tool = FunctionTool.from_defaults(name='detect_danger_tool',description="This tool that checks logs, detects danger ans query according to the input, it takes only one input of the type string",fn=detect_danger)
context1 = """
    Role: CyberSecurity Expert
    Instructions:
    - You have the tools file_expert_tool and create_logs_tool
    - Use file_expert_tool tool to get insights from the existing data
    - Get insigths and the audit report from file_expert_tool and generate a final cohesive report with valid information
    - Ensure all the user queries are answered in the answer
    - Use create_logs_tool to generate logs from the existing computer
    - Provide a complete answer with all the information gained in previous steps
    - Do not hallucinate context
    - Do not deviate from instructions
    - Do not use create_logs_tool unless specified by the user
    - Provide complete instructions for the file_expert_tool
"""
master_agent = ReActAgent.from_tools(tools = [create_logs_tool,file_expert_tool,detect_danger_tool],context=context1,llm=gemma_llm,max_iterations=50,verbose=True)
    

In [92]:
from llama_index.core.prompts import ChatMessage

gemma_llm = Gemini(model='models/gemini-1.5-flash-exp-0827')
def converttocsv():
    with open('Data\cybersecurity_logs.txt') as f:
        read_logs = f.read()
    messages = [ChatMessage(role="system",content="""
    Instructions:
    - From the input data, split into relevant columns and provide output as comma seperated values (csv)
    - The relevant columns from the unstructured data need to created
    - The data from unstructured data need to placed under the relevant columns
    - Do no hallucinate the data
    - Do not change the data from the user input
    - Do not hallucinate the columns names
    - Follow strictly the format of comma seperated values
    - Do not deviate from the instructions
    - Follow the instructions strictly
    Example:
    - Eg1:
     Input: Rajesh from 12 to 1 has created a Agentic RAG pilot
            Pranav from 2 to 3 has completed a Cybersecurity analysis
            Akbhar from 11-12 did a development improvement
            John in the span of 1-5 did got Clients on board
     Output: Name,time,work
             Rajesh,12-1,Agentic Rag pilot
             Pranav,2-3,Cybersecurity analysis
             Akbhar,11-12,Development
             John,1-5, Client Onboarding
    - Eg2: 
     Input:2024-09-22 15:09 Rs134 Rs133 Rs132
           2024-09-23 1:34 Rs1021.1 Rs956 Rs737
           2023-04-22 17:12 Rs1201 Rs420 Rs240
     Output:YYYY-MM-DD,HH:MM,High,Curremt,Low
            2024-09-22,15:09,Rs134,Rs133,Rs132
            2024-09-23,1:34,Rs1021.1,Rs956,Rs737
            2023-04-22,17:12,Rs1201,Rs420,Rs240
"""), ChatMessage(role="user",content=f"The below data given is a set of logs of process of a system, order them in a csv manner, Data: {read_logs}")]
    res = gemma_llm.chat(messages)

    return res

In [93]:
res = converttocsv()

In [46]:
print(res.message.content)

AttributeError: 'Response' object has no attribute 'message'

In [99]:
import pandas as pd

# with open('.\log_data.csv','x+') as f:
#     f.write(res.message.content)

df = pd.read_csv('.\log_data.csv')
df.head()

YYYY-MM-DD  HH:MM:SS                                     Process  \
0  2024-09-22  15:04:10       INFO Cybersecurity logging started...   
1  2024-09-22  15:04:11  INFO CPU Usage: 4.8% | Memory Usage: 51.2%   
2  2024-09-22  15:04:11                         INFO Process: PID=0   
3  2024-09-22  15:04:11                         INFO Process: PID=4   
4  2024-09-22  15:04:11                        INFO Process: PID=88   

                     Message                       User  
0                        NaN                        NaN  
1                        NaN                        NaN  
2   Name=System Idle Process   User=NT AUTHORITY\SYSTEM  
3                Name=System   User=NT AUTHORITY\SYSTEM  
4                      Name=                  User=None

In [2]:
with open('Data\cybersecurity_logs.txt','r') as f:
    temp = f.read()

temp = temp.strip()
temp

'2024-09-22 15:04:10,688 - INFO - Cybersecurity logging started...\n2024-09-22 15:04:11,693 - INFO - CPU Usage: 4.8% | Memory Usage: 51.2%\n2024-09-22 15:04:11,701 - INFO - Process: PID=0, Name=System Idle Process, User=NT AUTHORITY\\SYSTEM\n2024-09-22 15:04:11,791 - INFO - Process: PID=4, Name=System, User=NT AUTHORITY\\SYSTEM\n2024-09-22 15:04:11,796 - INFO - Process: PID=88, Name=, User=None\n2024-09-22 15:04:11,800 - INFO - Process: PID=156, Name=Registry, User=None\n2024-09-22 15:04:11,800 - INFO - Process: PID=516, Name=conhost.exe, User=PACMANEEE\\Pranav\n2024-09-22 15:04:11,804 - INFO - Process: PID=572, Name=smss.exe, User=None\n2024-09-22 15:04:11,809 - INFO - Process: PID=632, Name=winlogon.exe, User=None\n2024-09-22 15:04:11,813 - INFO - Process: PID=796, Name=services.exe, User=None\n2024-09-22 15:04:11,817 - INFO - Process: PID=824, Name=LsaIso.exe, User=None\n2024-09-22 15:04:11,821 - INFO - Process: PID=832, Name=svchost.exe, User=None\n2024-09-22 15:04:11,826 - INFO - 

In [8]:

import keras

input_layer = keras.layers.Input(shape=(1, 43))

# LSTM layers
x = keras.layers.LSTM(128, return_sequences=True,activation='relu')(input_layer)
x = keras.layers.Dropout(0.2)(x)
x = keras.layers.LSTM(64, return_sequences=True)(x)
x = keras.layers.Dropout(0.2)(x)
x = keras.layers.LSTM(32)(x)
x = keras.layers.Dropout(0.2)(x)

# Fully connected Dense layer
x = keras.layers.Dense(32, activation='relu')(x)

# Output for binary classification (label)
label_output = keras.layers.Dense(1, activation='sigmoid', name='label_output')(x)

# Output for multiclass classification (attack_cat)
attack_cat_output = keras.layers.Dense(10, activation='softmax', name='attack_cat_output')(x)


# Train the model
model_label = keras.Model(inputs=input_layer, outputs=[label_output])
model_cat = keras.Model(inputs=input_layer, outputs=[attack_cat_output])
model_label.compile(
    optimizer='adam',
    loss='binary_crossentropy',
    metrics=['accuracy']
)
model_cat.compile(
    optimizer='adam',
    loss='sparse_categorical_crossentropy',
    metrics=['accuracy']
)

model_cat.load_weights('cyber_sec_category.weights.h5')

model_label.load_weights(filepath='cyber_sec_label.weights.h5')

f:\Devfolio_hack\devfolio_hackathon-Cyber-AI\dev_env\Lib\site-packages\keras\src\saving\saving_lib.py:713: UserWarning: Skipping variable loading for optimizer 'adam', because it has 2 variables whereas the saved optimizer has 28 variables. 
  saveable.load_own_variables(weights_store.get(inner_path))


In [6]:
import pandas as pd
import numpy as np

X = pd.read_csv('UNSW_NB15_training-set.csv')
from sklearn.preprocessing import LabelEncoder, MinMaxScaler

label_encoders = {}
for col in ['proto', 'service', 'state', 'attack_cat']:
    le = LabelEncoder()
    X[col] = le.fit_transform(X[col])
    label_encoders[col] = le

scaler = MinMaxScaler()

y_cat = X['attack_cat']
X[X.columns] = scaler.fit_transform(X[X.columns])
# Normalize numerical columns using MinMaxScaler
y_label = X['label']
X = X.drop(columns=['label', 'attack_cat'])

X = np.array(X)
X = X.reshape((X.shape[0], 1, X.shape[1])) 

In [3]:
temp = np.expand_dims(X[0],axis=0)
temp.shape

(1, 1, 43)

In [16]:
preds = model_cat.predict(X,verbose=1)
count = 0
for i in range(len(preds)):
    pred = np.argmax(preds[i])
    if pred == y_cat[i]:
        count+=1
print(f"accuracy: {count/len(preds)}")

2573/2573 ━━━━━━━━━━━━━━━━━━━━ 4s 2ms/step
accuracy: 0.4742627410970218


In [89]:
model_label.evaluate(X,y_label)

2573/2573 ━━━━━━━━━━━━━━━━━━━━ 4s 2ms/step - accuracy: 0.9966 - loss: 0.0099


[0.005996870808303356, 0.9981781244277954]

In [1]:
def load_models():
    input_layer = keras.layers.Input(shape=(1, 43))

# LSTM layers
    x = keras.layers.LSTM(128, return_sequences=True,activation='relu')(input_layer)
    x = keras.layers.Dropout(0.2)(x)
    x = keras.layers.LSTM(64, return_sequences=True)(x)
    x = keras.layers.Dropout(0.2)(x)
    x = keras.layers.LSTM(32)(x)
    x = keras.layers.Dropout(0.2)(x)

    # Fully connected Dense layer
    x = keras.layers.Dense(32, activation='relu')(x)

    # Output for binary classification (label)
    label_output = keras.layers.Dense(1, activation='sigmoid', name='label_output')(x)

    # Output for multiclass classification (attack_cat)
    attack_cat_output = keras.layers.Dense(10, activation='softmax', name='attack_cat_output')(x)


    # Train the model
    model_label = keras.Model(inputs=input_layer, outputs=[label_output])
    model_cat = keras.Model(inputs=input_layer, outputs=[attack_cat_output])
    model_label.compile(
        optimizer='adam',
        loss='binary_crossentropy',
        metrics=['accuracy']
    )
    model_cat.compile(
        optimizer='adam',
        loss='sparse_categorical_crossentropy',
        metrics=['accuracy']
    )

    model_cat.load_weights('cyber_sec_category.weights.h5')

    model_label.load_weights(filepath='cyber_sec_label.weights.h5')

    return model_cat,model_label

In [4]:
def preprocess():
    X = pd.read_csv('UNSW_NB15_training-set.csv')
    label_encoders = {}
    for col in ['proto', 'service', 'state', 'attack_cat']:
        le = LabelEncoder()
        X[col] = le.fit_transform(X[col])
        label_encoders[col] = le

    scaler = MinMaxScaler()

    y_cat = X['attack_cat']
    X[X.columns] = scaler.fit_transform(X[X.columns])
    # Normalize numerical columns using MinMaxScaler
    y_label = X['label']
    X = X.drop(columns=['label', 'attack_cat'])

    X = np.array(X)
    X = X.reshape((X.shape[0], 1, X.shape[1])) 
    return X

In [10]:
from tqdm import tqdm

def detect_danger(input:str)->str:
    encoding = {'Analysis': 0, 'Backdoor': 1, 'DoS': 2, 'Exploits': 3, 'Fuzzers': 4, 'Generic': 5, 'Normal': 6, 'Reconnaissance': 7, 'Shellcode': 8, 'Worms': 9}
    res = {}
    X = preprocess()
    model_cat,model_label = load_models()
    preds = model_label.predict(X)
    cats = model_cat.predict(X)
    with open('LOG_DETECTS.txt','+a') as f:
        for i in tqdm(range(len(preds))):
            pred = 1 if preds[i] > 0.5 else 0
            temp = "Log is Normal\n"
            cat = None
            if pred == 1:
                for j,k in zip(encoding.values(),encoding.keys()):
                    if j == np.argmax(cats[i]):
                        cat = encoding[k]
                        break
                temp = f"The log {i} is suspicious with category {k}\n"
                print(temp)
            f.write(temp)
    reader = SimpleDirectoryReader(input_files=["LOG_DETECTS.txt"])
    documents = reader.load_data()

    splitter2 = SentenceSplitter(chunk_size = 2000,chunk_overlap=200)
    nodes = splitter2.get_nodes_from_documents(documents,show_progress=True)

    summary_index = SummaryIndex(nodes)
    sqe1 = summary_index.as_query_engine(llm=new_llm)
    res = sqe1.query(input)
    return res.response
    
